In [1]:
#pip install scrapy

In [2]:
import json

class JsonWriterPipeline(object):

    def open_spider(self, spider):
        self.file = open('reviewresult.jl', 'w')

    def close_spider(self, spider):
        self.file.close()

    def process_item(self, item, spider):
        line = json.dumps(dict(item)) + "\n"
        self.file.write(line)
        return item


In [3]:
from datetime import datetime, date
import logging
import time

import re

import scrapy

from scrapy.loader import ItemLoader
from scrapy.loader.processors import Compose, Join, MapCompose, TakeFirst
from scrapy.http import FormRequest, Request
from w3lib.url import url_query_parameter

class StripText:
    def __init__(self, chars=' \r\t\n'):
        self.chars = chars

    def __call__(self, value):
        try:
            return value.strip(self.chars)
        except:  
            return value
        
def str_to_float(x):
    x = x.replace(',', '')
    try:
        return float(x)
    except:  
        return x

def str_to_int(x):
    try:
        return int(str_to_float(x))
    except:  
        return x
    
def simplify_recommended(x):
    return True if x == 'Recommended' else False

def standardize_date(x):
    """
    Convert x from recognized input formats to desired output format,
    or leave unchanged if input format is not recognized.
    """
    fmt_fail = False

    for fmt in ['%b %d, %Y', '%B %d, %Y']:
        try:
            return datetime.strptime(x, fmt).strftime('%Y-%m-%d')
        except ValueError:
            fmt_fail = True

    # Induce year to current year if it is missing.
    for fmt in ['%b %d', '%B %d']:
        try:
            d = datetime.strptime(x, fmt)
            d = d.replace(year=date.today().year)
            return d.strftime('%Y-%m-%d')
        except ValueError:
            fmt_fail = True

    if fmt_fail:
        logger.debug(f'Could not process date {x}')

    return x


class ReviewItem(scrapy.Item):
    product_id = scrapy.Field()
    page = scrapy.Field()
    page_order = scrapy.Field()
    recommended = scrapy.Field(
        output_processor=Compose(TakeFirst(), simplify_recommended),
    )
    date = scrapy.Field(
        output_processor=Compose(TakeFirst(), standardize_date)
    )
    text = scrapy.Field(
        input_processor=MapCompose(StripText()),
        output_processor=Compose(Join('\n'), StripText())
    )
    hours = scrapy.Field(
        output_processor=Compose(TakeFirst(), str_to_float)
    )
    found_helpful = scrapy.Field(
        output_processor=Compose(TakeFirst(), str_to_int)
    )
    found_unhelpful = scrapy.Field(
        output_processor=Compose(TakeFirst(), str_to_int)
    )
    found_funny = scrapy.Field(
        output_processor=Compose(TakeFirst(), str_to_int)
    )
    compensation = scrapy.Field()
    username = scrapy.Field()
    user_id = scrapy.Field()
    products = scrapy.Field(
        output_processor=Compose(TakeFirst(), str_to_int)
    )
    early_access = scrapy.Field()
    
class ReviewItemLoader(ItemLoader):
    default_output_processor = TakeFirst()


def load_review(review, product_id, page, order):
    """
    Load a ReviewItem from a single review.
    """
    loader = ReviewItemLoader(ReviewItem(), review)

    loader.add_value('product_id', product_id)
    loader.add_value('page', page)
    loader.add_value('page_order', order)

    # Review data.
    loader.add_css('recommended', '.title::text')
    loader.add_css('date', '.date_posted::text', re='Posted: (.+)')
    loader.add_css('text', '.apphub_CardTextContent::text')
    loader.add_css('hours', '.hours::text', re='(.+) hrs')
    loader.add_css('compensation', '.received_compensation::text')

    # User/reviewer data.
    loader.add_css('user_id', '.apphub_CardContentAuthorName a::attr(href)', re='.*/profiles/(.+)/')
    loader.add_css('username', '.apphub_CardContentAuthorName a::text')
    loader.add_css('products', '.apphub_CardContentMoreLink ::text', re='([\d,]+) product')

    # Review feedback data.
    feedback = loader.get_css('.found_helpful ::text')
    loader.add_value('found_helpful', feedback, re='([\d,]+) of')
    loader.add_value('found_unhelpful', feedback, re='of ([\d,]+)')
    loader.add_value('found_funny', feedback, re='([\d,]+).*funny')

    early_access = loader.get_css('.early_access_review')
    if early_access:
        loader.add_value('early_access', True)
    else:
        loader.add_value('early_access', False)

    return loader.load_item()


def get_page(response):
    from_page = response.meta.get('from_page', None)

    if from_page:
        page = from_page + 1
    else:
        page = url_query_parameter(response.url, 'p', None)
        if page:
            page = str_to_int(page)

    return page


def get_product_id(response):
    product_id = response.meta.get('product_id', None)

    if not product_id:
        try:
            return re.findall("app/(.+?)/", response.url)[0]
        except:  
            return None
    else:
        return product_id

################################################################################################

class ReviewSpider(scrapy.Spider):
    name = 'reviews'
    start_urls = [
        # CS:GO
        'https://steamcommunity.com/app/730/reviews/?p=1&browsefilter=mostrecent',
    ]
    custom_settings = {
    'ITEM_PIPELINES': {'__main__.JsonWriterPipeline': 1},
    'FEED_FORMAT':'json',                                 
    'FEED_URI': 'reviewresult.json'
    }

    def __init__(self, url_file=None, steam_id=730, *args, **kwargs):
        super().__init__(*args, **kwargs)
        self.url_file = url_file
        self.steam_id = 730

    def read_urls(self):
        with open(self.url_file, 'r') as f:
            for url in f:
                url = url.strip()
                if url:
                    yield scrapy.Request(url, callback=self.parse)

    def start_requests(self):
        if self.steam_id:
            url = (
                f'http://steamcommunity.com/app/{self.steam_id}/reviews/'
                '?browsefilter=mostrecent&p=1'
            )
            yield Request(url, callback=self.parse)
        elif self.url_file:
            yield from self.read_urls()
        else:
            for url in self.test_urls:
                yield Request(url, callback=self.parse)

    def parse(self, response):
        page = get_page(response)
        product_id = get_product_id(response)

        # Load all reviews on current page.
        reviews = response.css('div .apphub_Card')
        for i, review in enumerate(reviews):
            yield load_review(review, product_id, page, i)

        # Navigate to next page.
        form = response.xpath('//form[contains(@id, "MoreContentForm")]')
        if form:
            yield self.process_pagination_form(form, page, product_id)

    def process_pagination_form(self, form, page=None, product_id=None):
        action = form.xpath('@action').extract_first()
        names = form.xpath('input/@name').extract()
        values = form.xpath('input/@value').extract()

        formdata = dict(zip(names, values))
        meta = dict(prev_page=page, product_id=product_id)

        return FormRequest(
            url=action,
            method='GET',
            formdata=formdata,
            callback=self.parse,
            meta=meta
        )

/opt/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:73: ScrapyDeprecationWarning: scrapy.loader.processors.TakeFirst is deprecated, instantiate itemloaders.processors.TakeFirst instead.
/opt/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:73: ScrapyDeprecationWarning: scrapy.loader.processors.Compose is deprecated, instantiate itemloaders.processors.Compose instead.
/opt/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:76: ScrapyDeprecationWarning: scrapy.loader.processors.TakeFirst is deprecated, instantiate itemloaders.processors.TakeFirst instead.
/opt/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:76: ScrapyDeprecationWarning: scrapy.loader.processors.Compose is deprecated, instantiate itemloaders.processors.Compose instead.
/opt/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:79: ScrapyDeprecationWarning: scrapy.loader.processors.MapCompose is deprecated, instantiate itemloaders.processors.MapCompose instead.
/opt/anacon

In [4]:
from scrapy.crawler import CrawlerProcess

process = CrawlerProcess({
    'USER_AGENT': 'Mozilla/4.0 (compatible; MSIE 7.0; Windows NT 5.1)'
})

process.crawl(ReviewSpider)
process.start()

2021-01-10 19:10:27 [scrapy.utils.log] INFO: Scrapy 2.4.1 started (bot: scrapybot)
2021-01-10 19:10:27 [scrapy.utils.log] INFO: Versions: lxml 4.5.0.0, libxml2 2.9.9, cssselect 1.1.0, parsel 1.6.0, w3lib 1.22.0, Twisted 20.3.0, Python 3.7.6 (default, Jan  8 2020, 13:42:34) - [Clang 4.0.1 (tags/RELEASE_401/final)], pyOpenSSL 19.1.0 (OpenSSL 1.1.1d  10 Sep 2019), cryptography 2.8, Platform Darwin-19.5.0-x86_64-i386-64bit
2021-01-10 19:10:27 [scrapy.utils.log] DEBUG: Using reactor: twisted.internet.selectreactor.SelectReactor
2021-01-10 19:10:27 [scrapy.crawler] INFO: Overridden settings:
{'USER_AGENT': 'Mozilla/4.0 (compatible; MSIE 7.0; Windows NT 5.1)'}
2021-01-10 19:10:27 [scrapy.extensions.telnet] INFO: Telnet Password: c4798d90c0d3fabc
2021-01-10 19:10:27 [py.warnings] WARNING: /opt/anaconda3/lib/python3.7/site-packages/scrapy/extensions/feedexport.py:247: ScrapyDeprecationWarning: The `FEED_URI` and `FEED_FORMAT` settings have been deprecated in favor of the `FEEDS` setting. Please

2021-01-10 19:10:29 [scrapy.core.scraper] DEBUG: Scraped from <200 https://steamcommunity.com/app/730/homecontent/?userreviewscursor=AoJw98ys9%2FYCcviYwgI%3D&userreviewsoffset=10&p=2&workshopitemspage=2&readytouseitemspage=2&mtxitemspage=2&itemspage=2&screenshotspage=2&videospage=2&artpage=2&allguidepage=2&webguidepage=2&integratedguidepage=2&discussionspage=2&numperpage=10&browsefilter=mostrecent&l=english&appHubSubSection=10&filterLanguage=default&searchText=&forceanon=1>
{'date': '2021-01-10',
 'early_access': False,
 'hours': 359.9,
 'page': 2,
 'page_order': 1,
 'product_id': '730',
 'products': 12,
 'recommended': False,
 'text': 'THIS GAME IS TRASH',
 'user_id': '76561198367245317',
 'username': 'Clishoo'}
2021-01-10 19:10:29 [scrapy.core.scraper] DEBUG: Scraped from <200 https://steamcommunity.com/app/730/homecontent/?userreviewscursor=AoJw98ys9%2FYCcviYwgI%3D&userreviewsoffset=10&p=2&workshopitemspage=2&readytouseitemspage=2&mtxitemspage=2&itemspage=2&screenshotspage=2&videosp

2021-01-10 19:10:29 [scrapy.core.scraper] DEBUG: Scraped from <200 https://steamcommunity.com/app/730/homecontent/?userreviewscursor=AoJ45%2Fim9%2FYCd7mYwgI%3D&userreviewsoffset=20&p=3&workshopitemspage=3&readytouseitemspage=3&mtxitemspage=3&itemspage=3&screenshotspage=3&videospage=3&artpage=3&allguidepage=3&webguidepage=3&integratedguidepage=3&discussionspage=3&numperpage=10&browsefilter=mostrecent&appid=730&appHubSubSection=10&l=english&filterLanguage=default&searchText=&forceanon=1>
{'date': '2021-01-10',
 'early_access': False,
 'hours': 274.3,
 'page': 3,
 'page_order': 2,
 'product_id': '730',
 'recommended': True,
 'text': 'Good game good game',
 'user_id': '76561199076852655',
 'username': 'SOLDIER 2K'}
2021-01-10 19:10:29 [scrapy.core.scraper] DEBUG: Scraped from <200 https://steamcommunity.com/app/730/homecontent/?userreviewscursor=AoJ45%2Fim9%2FYCd7mYwgI%3D&userreviewsoffset=20&p=3&workshopitemspage=3&readytouseitemspage=3&mtxitemspage=3&itemspage=3&screenshotspage=3&videosp

2021-01-10 19:10:30 [scrapy.core.scraper] DEBUG: Scraped from <200 https://steamcommunity.com/app/730/homecontent/?userreviewscursor=AoJ4upOj9%2FYCco%2BYwgI%3D&userreviewsoffset=30&p=4&workshopitemspage=4&readytouseitemspage=4&mtxitemspage=4&itemspage=4&screenshotspage=4&videospage=4&artpage=4&allguidepage=4&webguidepage=4&integratedguidepage=4&discussionspage=4&numperpage=10&browsefilter=mostrecent&appid=730&appHubSubSection=10&l=english&filterLanguage=default&searchText=&forceanon=1>
{'date': '2021-01-10',
 'early_access': False,
 'hours': 267.4,
 'page': 4,
 'page_order': 2,
 'product_id': '730',
 'products': 4,
 'recommended': True,
 'text': 'l',
 'user_id': '76561198386098026',
 'username': 'csgoroll.com'}
2021-01-10 19:10:30 [scrapy.core.scraper] DEBUG: Scraped from <200 https://steamcommunity.com/app/730/homecontent/?userreviewscursor=AoJ4upOj9%2FYCco%2BYwgI%3D&userreviewsoffset=30&p=4&workshopitemspage=4&readytouseitemspage=4&mtxitemspage=4&itemspage=4&screenshotspage=4&videosp

2021-01-10 19:10:31 [scrapy.core.scraper] DEBUG: Scraped from <200 https://steamcommunity.com/app/730/homecontent/?userreviewscursor=AoJwpOie9%2FYCddyXwgI%3D&userreviewsoffset=40&p=5&workshopitemspage=5&readytouseitemspage=5&mtxitemspage=5&itemspage=5&screenshotspage=5&videospage=5&artpage=5&allguidepage=5&webguidepage=5&integratedguidepage=5&discussionspage=5&numperpage=10&browsefilter=mostrecent&appid=730&appHubSubSection=10&l=english&filterLanguage=default&searchText=&forceanon=1>
{'date': '2021-01-10',
 'early_access': False,
 'hours': 50.4,
 'page': 5,
 'page_order': 2,
 'product_id': '730',
 'products': 57,
 'recommended': True,
 'text': "it's cs",
 'username': 'bibi_bate'}
2021-01-10 19:10:31 [scrapy.core.scraper] DEBUG: Scraped from <200 https://steamcommunity.com/app/730/homecontent/?userreviewscursor=AoJwpOie9%2FYCddyXwgI%3D&userreviewsoffset=40&p=5&workshopitemspage=5&readytouseitemspage=5&mtxitemspage=5&itemspage=5&screenshotspage=5&videospage=5&artpage=5&allguidepage=5&web

...

2021-01-10 19:19:04 [scrapy.core.scraper] DEBUG: Scraped from <200 https://steamcommunity.com/app/730/homecontent/?userreviewscursor=AoJ41dLE5PYCfviOwAI%3D&userreviewsoffset=6488&p=650&workshopitemspage=650&readytouseitemspage=650&mtxitemspage=650&itemspage=650&screenshotspage=650&videospage=650&artpage=650&allguidepage=650&webguidepage=650&integratedguidepage=650&discussionspage=650&numperpage=10&browsefilter=mostrecent&appid=730&appHubSubSection=10&l=english&filterLanguage=default&searchText=&forceanon=1>
{'date': '2021-01-03',
 'early_access': False,
 'hours': 191.9,
 'page': 650,
 'page_order': 8,
 'product_id': '730',
 'recommended': True,
 'text': 'banger',
 'user_id': '76561199004613477',
 'username': 'n1'}
2021-01-10 19:19:04 [scrapy.core.scraper] DEBUG: Scraped from <200 https://steamcommunity.com/app/730/homecontent/?userreviewscursor=AoJ41dLE5PYCfviOwAI%3D&userreviewsoffset=6488&p=650&workshopitemspage=650&readytouseitemspage=650&mtxitemspage=650&itemspage=650&screenshotspag

2021-01-10 19:19:04 [scrapy.core.scraper] DEBUG: Scraped from <200 https://steamcommunity.com/app/730/homecontent/?userreviewscursor=AoJwj7HC5PYCd8%2BOwAI%3D&userreviewsoffset=6498&p=651&workshopitemspage=651&readytouseitemspage=651&mtxitemspage=651&itemspage=651&screenshotspage=651&videospage=651&artpage=651&allguidepage=651&webguidepage=651&integratedguidepage=651&discussionspage=651&numperpage=10&browsefilter=mostrecent&appid=730&appHubSubSection=10&l=english&filterLanguage=default&searchText=&forceanon=1>
{'date': '2021-01-03',
 'early_access': False,
 'hours': 271.4,
 'page': 651,
 'page_order': 8,
 'product_id': '730',
 'products': 6,
 'recommended': True,
 'text': 'Un joc jucabil',
 'user_id': '76561198803033730',
 'username': 'Senpai'}
2021-01-10 19:19:04 [scrapy.core.scraper] DEBUG: Scraped from <200 https://steamcommunity.com/app/730/homecontent/?userreviewscursor=AoJwj7HC5PYCd8%2BOwAI%3D&userreviewsoffset=6498&p=651&workshopitemspage=651&readytouseitemspage=651&mtxitemspage=

2021-01-10 19:19:05 [scrapy.core.scraper] DEBUG: Scraped from <200 https://steamcommunity.com/app/730/homecontent/?userreviewscursor=AoJwm7PA5PYCeqeOwAI%3D&userreviewsoffset=6508&p=652&workshopitemspage=652&readytouseitemspage=652&mtxitemspage=652&itemspage=652&screenshotspage=652&videospage=652&artpage=652&allguidepage=652&webguidepage=652&integratedguidepage=652&discussionspage=652&numperpage=10&browsefilter=mostrecent&appid=730&appHubSubSection=10&l=english&filterLanguage=default&searchText=&forceanon=1>
{'date': '2021-01-03',
 'early_access': False,
 'hours': 534.7,
 'page': 652,
 'page_order': 8,
 'product_id': '730',
 'products': 1,
 'recommended': True,
 'text': 'Best',
 'username': 'Bedo'}
2021-01-10 19:19:05 [scrapy.core.scraper] DEBUG: Scraped from <200 https://steamcommunity.com/app/730/homecontent/?userreviewscursor=AoJwm7PA5PYCeqeOwAI%3D&userreviewsoffset=6508&p=652&workshopitemspage=652&readytouseitemspage=652&mtxitemspage=652&itemspage=652&screenshotspage=652&videospage=

2021-01-10 19:19:06 [scrapy.core.scraper] DEBUG: Scraped from <200 https://steamcommunity.com/app/730/homecontent/?userreviewscursor=AoJ44I2%2B5PYCdfuNwAI%3D&userreviewsoffset=6518&p=653&workshopitemspage=653&readytouseitemspage=653&mtxitemspage=653&itemspage=653&screenshotspage=653&videospage=653&artpage=653&allguidepage=653&webguidepage=653&integratedguidepage=653&discussionspage=653&numperpage=10&browsefilter=mostrecent&appid=730&appHubSubSection=10&l=english&filterLanguage=default&searchText=&forceanon=1>
{'date': '2021-01-03',
 'early_access': False,
 'hours': 299.3,
 'page': 653,
 'page_order': 8,
 'product_id': '730',
 'products': 3,
 'recommended': True,
 'text': 'good',
 'user_id': '76561198367934347',
 'username': 'RazVyVy_GG/Hellcase.com'}
2021-01-10 19:19:06 [scrapy.core.scraper] DEBUG: Scraped from <200 https://steamcommunity.com/app/730/homecontent/?userreviewscursor=AoJ44I2%2B5PYCdfuNwAI%3D&userreviewsoffset=6518&p=653&workshopitemspage=653&readytouseitemspage=653&mtxite

2021-01-10 19:19:07 [scrapy.core.scraper] DEBUG: Scraped from <200 https://steamcommunity.com/app/730/homecontent/?userreviewscursor=AoJw2qq85PYCfNWNwAI%3D&userreviewsoffset=6528&p=654&workshopitemspage=654&readytouseitemspage=654&mtxitemspage=654&itemspage=654&screenshotspage=654&videospage=654&artpage=654&allguidepage=654&webguidepage=654&integratedguidepage=654&discussionspage=654&numperpage=10&browsefilter=mostrecent&appid=730&appHubSubSection=10&l=english&filterLanguage=default&searchText=&forceanon=1>
{'date': '2021-01-03',
 'early_access': False,
 'hours': 14.2,
 'page': 654,
 'page_order': 8,
 'product_id': '730',
 'products': 6,
 'recommended': True,
 'text': 'It kicked me because of amd fps software, why?',
 'user_id': '76561199002491401',
 'username': 'TheMovingTargetMain'}
2021-01-10 19:19:07 [scrapy.core.scraper] DEBUG: Scraped from <200 https://steamcommunity.com/app/730/homecontent/?userreviewscursor=AoJw2qq85PYCfNWNwAI%3D&userreviewsoffset=6528&p=654&workshopitemspage=6

In [6]:
import pandas as pd
df = pd.read_json('reviewresult.json')
df

product_id  page  page_order  recommended       date  \
0            730     1           0        False 2021-01-10   
1            730     1           1         True 2021-01-10   
2            730     1           2         True 2021-01-10   
3            730     1           3         True 2021-01-10   
4            730     1           4         True 2021-01-10   
...          ...   ...         ...          ...        ...   
6533         730   654           5        False 2021-01-03   
6534         730   654           6         True 2021-01-03   
6535         730   654           7         True 2021-01-03   
6536         730   654           8         True 2021-01-03   
6537         730   654           9         True 2021-01-03   

                                                   text  hours       user_id  \
0                         sehit game addictive but ♥♥♥♥   72.9  7.656120e+16   
1     It's an experience you can't really get on any...   56.4           NaN   
2                                      Full of cheaters   37.3           NaN   
3                                   is good cuz is good   65.8           NaN   
4                                                  yes.   17.1           NaN   
...                                                 ...    ...           ...   
6533  Your VAC ban in Counter-Strike: Global Offensi...  128.5           NaN   
6534                                     Good game . GJ  764.1           NaN   
6535                     GOOD WAY TO NOT GO INSANE HAHA  656.7  7.656120e+16   
6536     It kicked me because of amd fps software, why?   14.2  7.656120e+16   
6537                                               good  157.6  7.656120e+16   

                 username  products  early_access compensation  found_funny  
0                   Pingu       2.0         False          NaN          NaN  
1              TinCan9545      80.0         False          NaN          NaN  
2                    Gare       1.0         False          NaN          NaN  
3           S3cr37_Sn1p3r       3.0         False          NaN          NaN  
4                    zehx      15.0         False          NaN          NaN  
...                   ...       ...           ...          ...          ...  
6533                 veke       1.0         False          NaN          NaN  
6534               Glowck       2.0         False          NaN          NaN  
6535  Mali "Ž" (Little Ž)      23.0         False          NaN          NaN  
6536  TheMovingTargetMain       6.0         False          NaN          NaN  
6537                  (8)       NaN         False          NaN          NaN  

[6538 rows x 13 columns]